# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO) [15 EVs per week test]

Installing required packages and dependencies

In [ ]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [ ]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

In [ ]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.15
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.15', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.15\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [ ]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [ ]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f1d65b99850>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 15
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 15, 'EVs_n_max': 783, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_energ

In [ ]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
#env.plot_VPP_input_data()

Charging event: 1, Arrival time: 2022-01-02 21:00:00, Parking_time: 24, Leaving_time: 2022-01-03 21:00:00, SOC: 0.4251772453050117, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 783, Arrival time: 2022-12-31 23:30:00, Parking_time: 22.58897578895077, Leaving_time: 2023-01-01 22:05:20.312840, SOC: 0.4614636540200397, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -21214.64 , Grid_used_en(grid-import)=4947.18kWh , autarky-rate=83.0 , RE-to-vehicle_unused_en(grid-export)=-26161.81kWh , self-consump.rate=47.9 , Total_selling_cost=€  -489.75 , Grid_cost=€  233.11
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  14027.15 , Grid_used_en=kWh  32419.4 , RE-to-vehicle_unused_en=kWh  18392.25 , Total_selling_cost=€  614.91 , Grid_cost=€  1147.7 , Charging_events=  783 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  83.41


In [ ]:
env.plot_ELVIS_data()

In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
#env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13981.08 , Grid_used_en(grid-import)=32645.94kWh , Total_demand=64215.97kWh , autarky-rate=49.2 , RE-to-vehicle_unused_en(grid-export)=18664.86kWh , Total_supply=50234.89kWh , self-consump.rate=62.8 , Grid_cost=€  1180.95 , Total_selling_cost=€  655.75 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  83.41
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [ ]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_autarky()

In [ ]:
#env.plot_Elvis_results()

In [ ]:
#env.plot_VPP_results()

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [ ]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  14117.84 , Grid_used_en(grid-import)=32926.13kWh , Total_demand=64375.24kWh , autarky-rate=48.9 , RE-to-vehicle_unused_en(grid-export)=18808.29kWh , Total_supply=50257.4kWh , self-consump.rate=62.6 , Grid_cost=€  1205.85 , Total_selling_cost=€  667.46 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  83.41
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -6836.17 , Grid_used_en(grid-import)=2725.74kWh , Total_demand=54122.61kWh , autarky-rate=95.0 , RE-to-vehicle_unused_en(grid-export)=9561.91kWh , Total_supply=60958.78kWh , self-consump.rate=84.3 , Total_selling_cost=€  -142.61 , Grid_cost=€  90.3 
 EV_INFO: Av.EV_energy_leaving=kWh  68.68 , Std.EV_energy_leaving=kWh  24.48 , EV_departures =  783 , EV_queue_left =  0
SCORE:  Cumulative_reward= 319692.51 - Step_rewars (load_t= 295524.55, EVs_ener

In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  46.750603  45.717503  50.607922  41.901886   
2022-01-01 00:15:00  47.000603  45.102654  49.993073  42.151886   
2022-01-01 00:30:00  47.250603  44.652512  49.542931  42.401886   
2022-01-01 00:45:00  47.500603  44.096966  48.987385  42.651886   
2022-01-01 01:00:00  47.750603  43.715103  48.605522  42.901886   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00   0.000000  78.179497  60.006191  72.971672   
2022-06-06 05:00:00   0.000000  79.260963  61.087658  74.053139   
2022-06-06 05:15:00   0.000000  80.234337  62.061031  75.026512   
2022-06-06 05:30:00   0.000000  81.261894  63.088593  76.054070   
2022-06-06 05:45:00   0.000000  82.241692  64.068390  77.033867   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00  [2347, 2345, 2346, 2344]  [1, 2, 2, 1]   
2022-01-01 00:30:00  [2347, 2345, 2346, 2344]  [1, 2, 2, 1]   
2022-01-01 00:45:00  [2347, 2345, 2346, 2344]  [1, 2, 2, 1]   
2022-01-01 01:00:00  [2347, 2345, 2346, 2344]  [1, 2, 2, 1]   
...                                       ...           ...   
2022-06-06 04:45:00     [0, 2681, 2683, 2682]  [2, 1, 1, 1]   
2022-06-06 05:00:00     [0, 2681, 2683, 2682]  [2, 1, 1, 1]   
2022-06-06 05:15:00     [0, 2681, 2683, 2682]  [2, 1, 1, 1]   
2022-06-06 05:30:00     [0, 2681, 2683, 2682]  [2, 1, 1, 1]   
2022-06-06 05:45:00     [0, 2681, 2683, 2682]  [2, 1, 1, 1]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00    [False, True, True, False]        2.000000   
2022-01-01 00:30:00    [False, True, True, False]        2.000000   
2022-01-01 00:45:00    [False, True, True, False]        2.000000   
2022-01-01 01:00:00    [False, True, True, False]        2.000000   
...                                           ...             ...   
2022-06-06 04:45:00     [False, True, True, True]        9.130868   
2022-06-06 05:00:00     [False, True, True, True]       12.977589   
2022-06-06 05:15:00     [False, True, True, True]       11.680462   
2022-06-06 05:30:00     [False, True, True, True]       12.330724   
2022-06-06 05:45:00     [False, True, True, True]       11.757602   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00           0.000000  1.813830e+00         15.0        0.0   
2022-01-01 00:15:00          -4.918802  0.000000e+00         15.0        0.0   
2022-01-01 00:30:00          -3.601141  2.220446e-16         15.0        0.0   
2022-01-01 00:45:00          -4.444379  0.000000e+00         15.0        0.0   
2022-01-01 01:00:00          -3.054899  0.000000e+00         15.0        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00           0.000000  0.000000e+00         15.0        0.0   
2022-06-06 05:00:00           0.000000  0.000000e+00         15.0        0.0   
2022-06-06 05:15:00           0.000000  0.000000e+00         15.0        0.0   
2022-06-06 05:30:00           0.000000 -1.776357e-15         15.0        0.0   
2022-06-06 05:45:00           0.000000  0.000000e+00         15.0        0.0   

                     rewards  
time                          
2022-01-01 00:00:00     15.0  
2022-01-01 00:15:00     15.0  
2022-01-01 00:30:00     15.0  
2022-01-01 00:45:00     15.0  
2022-01-01 01:00:00     15.0  
...                      ...  
2022-06-06 04:45:00     15.0  
2022-06-06 05:00:00     15.0  
2022-06-06 05:15:00     15.0  
2022-06-06 05:30:00     15.0  
2022-06-06 05:45:00     15

In [ ]:
env.plot_VPP_autarky()

In [ ]:
#env.plot_Elvis_results()

In [ ]:
#env.plot_VPP_results()

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [ ]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 3133, Arrival time: 2022-01-01 10:45:00, Parking_time: 23.737639061186442, Leaving_time: 2022-01-02 10:29:15.500620, SOC: 0.2772312376588949, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 3915, Arrival time: 2022-12-31 10:00:00, Parking_time: 21.510071866970435, Leaving_time: 2023-01-01 07:30:36.258721, SOC: 0.5374311197289585, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , Grid_used_en(grid-import)=2136.67kWh , autarky-rate=89.6 , RE-to-vehicle_unused_en(grid-export)=-32222.06kWh , self-consump.rate=36.4 , Total_selling_cost=€  -1187.15 , Grid_cost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  4474.94 , Grid_used_en=kWh  28176.24 , RE-to-vehicle_unused_en=kWh  23701.3 , Total_selling_cost=€  304.43 , Grid_cost=€  1258.82 , Charging_events=  783 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  91.15


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
#env.plot_VPP_input_data()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  4326.39 , Grid_used_en(grid-import)=28070.94kWh , Total_demand=54956.88kWh , autarky-rate=48.9 , RE-to-vehicle_unused_en(grid-export)=23744.55kWh , Total_supply=50630.48kWh , self-consump.rate=53.1 , Grid_cost=€  1232.32 , Total_selling_cost=€  272.25 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  91.15
Simulating VPP....


In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  4940.45 , Grid_used_en(grid-import)=28134.6kWh , Total_demand=55545.8kWh , autarky-rate=49.3 , RE-to-vehicle_unused_en(grid-export)=23194.15kWh , Total_supply=50605.35kWh , self-consump.rate=54.2 , Grid_cost=€  1214.94 , Total_selling_cost=€  274.93 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  91.15
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -10225.1 , Grid_used_en(grid-import)=1676.56kWh , Total_demand=48403.8kWh , autarky-rate=96.5 , RE-to-vehicle_unused_en(grid-export)=11901.66kWh , Total_supply=58628.9kWh , self-consump.rate=79.7 , Total_selling_cost=€  -391.69 , Grid_cost=€  72.77 
 EV_INFO: Av.EV_energy_leaving=kWh  75.61 , Std.EV_energy_leaving=kWh  22.06 , EV_departures =  778 , EV_queue_left =  1
SCORE:  Cumulative_reward= 331505.49 - Step_rewars (load_t= 284041.73, EVs_energy

In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  96.383369  75.204948  48.554882  60.274742   
2022-06-06 05:00:00  97.276932  76.098511  49.448448  61.168308   
2022-06-06 05:15:00  98.136116  76.957695  50.307632  62.027493   
2022-06-06 05:30:00  99.079674  77.901253  51.251190  62.971050   
2022-06-06 05:45:00  99.970406  78.791985  52.141922  63.861782   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
...                                       ...           ...   
2022-06-06 04:45:00  [5045, 5046, 5047, 5048]  [1, 1, 1, 1]   
2022-06-06 05:00:00  [5045, 5046, 5047, 5048]  [1, 1, 1, 1]   
2022-06-06 05:15:00  [5045, 5046, 5047, 5048]  [1, 1, 1, 1]   
2022-06-06 05:30:00  [5045, 5046, 5047, 5048]  [1, 1, 1, 1]   
2022-06-06 05:45:00  [5045, 5046, 5047, 5048]  [1, 1, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00  [False, False, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 04:45:00    [False, True, True, True]       10.867787   
2022-06-06 05:00:00    [False, True, True, True]       14.297029   
2022-06-06 05:15:00    [False, True, True, True]       13.746956   
2022-06-06 05:30:00    [False, True, True, True]       15.096917   
2022-06-06 05:45:00    [False, True, True, True]       14.251701   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -3.637928    -5.560300        0.0   
2022-01-01 00:15:00                0.0 -4.616330    -4.839817        0.0   
2022-01-01 00:30:00                0.0 -3.903890    -3.594845        0.0   
2022-01-01 00:45:00                0.0 -3.156907    -3.148232        0.0   
2022-01-01 01:00:00                0.0 -2.888939    -5.195137        0.0   
...                                ...       ...          ...        ...   
2022-06-06 04:45:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:00:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:15:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:30:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:45:00                0.0  0.000000    -4.526264        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -5.560300  
2022-01-01 00:15:00  -4.839817  
2022-01-01 00:30:00  -3.594845  
2022-01-01 00:45:00  -3.148232  
2022-01-01 01:00:00  -5.195137  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
2022-06-06 05:45:00  -4.526264  

[15000 rows x 13 columns]

In [ ]:
env.plot_VPP_autarky()

In [ ]:
#env.plot_VPP_results()


In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [ ]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 5482, Arrival time: 2022-01-01 10:45:00, Parking_time: 24, Leaving_time: 2022-01-02 10:45:00, SOC: 0.49052851923949164, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 6264, Arrival time: 2022-12-31 18:45:00, Parking_time: 23.72498161382937, Leaving_time: 2023-01-01 18:28:29.933810, SOC: 0.41353182662715304, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , Grid_used_en(grid-import)=1556.25kWh , autarky-rate=90.5 , RE-to-vehicle_unused_en(grid-export)=-35673.95kWh , self-consump.rate=29.4 , Total_selling_cost=€  -1196.64 , Grid_cost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  1278.1 , Grid_used_en=kWh  25793.45 , RE-to-vehicle_unused_en=kWh  24515.35 , Total_selling_cost=€  208.81 , Grid_cost=€  1099.35 , Charging_events=  783 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  95.56


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
#env.plot_VPP_input_data()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  1253.15 , Grid_used_en(grid-import)=26689.14kWh , Total_demand=51759.57kWh , autarky-rate=48.4 , RE-to-vehicle_unused_en(grid-export)=25435.99kWh , Total_supply=50506.43kWh , self-consump.rate=49.6 , Grid_cost=€  1129.77 , Total_selling_cost=€  203.55 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  95.56
Simulating VPP....


In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  518.16 , Grid_used_en(grid-import)=26298.77kWh , Total_demand=51016.2kWh , autarky-rate=48.5 , RE-to-vehicle_unused_en(grid-export)=25780.61kWh , Total_supply=50498.05kWh , self-consump.rate=48.9 , Grid_cost=€  1112.05 , Total_selling_cost=€  169.67 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  95.56
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -13497.38 , Grid_used_en(grid-import)=1333.48kWh , Total_demand=44914.6kWh , autarky-rate=97.0 , RE-to-vehicle_unused_en(grid-export)=14830.86kWh , Total_supply=58411.98kWh , self-consump.rate=74.6 , Total_selling_cost=€  -465.97 , Grid_cost=€  56.7 
 EV_INFO: Av.EV_energy_leaving=kWh  77.0 , Std.EV_energy_leaving=kWh  22.36 , EV_departures =  781 , EV_queue_left =  0
SCORE:  Cumulative_reward= 306922.69 - Step_rewars (load_t= 258577.44, EVs_energy

In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(14995)

0    1    2    3        EVs_id       actions  \
time                                                                  
2022-01-01 00:00:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 0, 1, 0]   
...                  ...  ...  ...  ...           ...           ...   
2022-06-06 03:30:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 0, 1, 0]   
2022-06-06 03:45:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 0, 1, 0]   
2022-06-06 04:00:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 0, 1, 0]   
2022-06-06 04:15:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 0, 1, 0]   
2022-06-06 04:30:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 0, 1, 0]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]             0.0   
2022-01-01 00:15:00  [False, False, False, True]             0.0   
2022-01-01 00:30:00  [False, False, False, True]             0.0   
2022-01-01 00:45:00  [False, False, False, True]             0.0   
2022-01-01 01:00:00   [False, True, False, True]             0.0   
...                                          ...             ...   
2022-06-06 03:30:00   [False, True, False, True]             0.0   
2022-06-06 03:45:00   [False, True, False, True]             0.0   
2022-06-06 04:00:00   [False, True, False, True]             0.0   
2022-06-06 04:15:00   [False, True, False, True]             0.0   
2022-06-06 04:30:00   [False, True, False, True]             0.0   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -3.812207    -3.414042        0.0   
2022-01-01 00:15:00                0.0 -3.048425    -5.057106        0.0   
2022-01-01 00:30:00                0.0 -4.062817    -4.375532        0.0   
2022-01-01 00:45:00                0.0 -3.625319    -6.405101        0.0   
2022-01-01 01:00:00                0.0 -5.545611    -6.822285        0.0   
...                                ...       ...          ...        ...   
2022-06-06 03:30:00                0.0 -3.724535    -5.389828        0.0   
2022-06-06 03:45:00                0.0 -4.428810    -7.276958        0.0   
2022-06-06 04:00:00                0.0 -6.504653    -6.227490        0.0   
2022-06-06 04:15:00                0.0 -5.350239    -7.110294        0.0   
2022-06-06 04:30:00                0.0 -6.321324    -6.651111        0.0   

                      rewards  
time                           
2022-01-01 00:00:00 -3.414042  
2022-01-01 00:15:00 -5.057106  
2022-01-01 00:30:00 -4.375532  
2022-01-01 00:45:00 -6.405101  
2022-01-01 01:00:00 -6.822285  
...                       ...  
2022-06-06 03:30:00 -5.389828  
2022-06-06 03:45:00 -7.276958  
2022-06-06 04:00:00 -6.227490  
2022-06-06 04:15:00 -7.110294  
2022-06-06 04:30:00 -6.651111  

[14995 rows x 13 columns]

In [ ]:
env.plot_VPP_autarky()

In [ ]:
#env.plot_VPP_results()

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#env.close()